In [79]:
import pandas as pd
import numpy as np
import plotly.express as px
from sklearn.ensemble import RandomForestRegressor


# Import to add project folder to sys path
import sys
utils_path = '/Users/Ryan/Documents/projects/ncaa-basketball/code/utils'
if utils_path not in sys.path:
    sys.path.append(utils_path)
    
from api import opponentAdjust
from db import get_db


In [2]:
firstYr = True
for yr in range(2003,2021):
    print(f"Reading in {yr}'s data")
    if firstYr:
        raw = pd.read_csv(f"/Users/Ryan/Documents/projects/ncaa-basketball/data/predate_games/{yr}.csv")
        firstYr = False
    else:
        raw = raw.append(pd.read_csv(f"/Users/Ryan/Documents/projects/ncaa-basketball/data/predate_games/{yr}.csv"))


Reading in 2003's data
Reading in 2004's data
Reading in 2005's data
Reading in 2006's data
Reading in 2007's data
Reading in 2008's data
Reading in 2009's data
Reading in 2010's data
Reading in 2011's data
Reading in 2012's data
Reading in 2013's data
Reading in 2014's data
Reading in 2015's data
Reading in 2016's data
Reading in 2017's data
Reading in 2018's data
Reading in 2019's data
Reading in 2020's data


In [36]:
df = raw.copy()

We cam take a look at the breakdown of team-date records for each number of games played to date

In [5]:
#fig = px.histogram(df, x='isRegularSeason')
#fig.show()

Let's normalize all of our metrics by 40 minutes and delete a lot of extra columns

In [37]:
METRICS = [
    'PF', 'Margin',
    'FGM', 'FGA',
    'FG3M', 'FG3A',
    'FG2M', 'FG2A',
    'FTA', 'FTM',
    'Ast', 'ORB',
    'DRB', 'TRB',
    'TO', 'Stl',
    'Blk', 'Foul'
]
PREFIXES= ['Tm', 'Opp']


df = opponentAdjust(df, PREFIXES, METRICS, includeOARankFields=False, includeNormRankFields=False, includeNormFields=True)
df['TmWinPct'] = df['TmWin'] / df['TmGame']
df['TmPossPerGame'] = df['TmPoss'] / df['TmGame']

In [38]:
for x in ['TmWin', 'TmMins', 'OppGame', 'TmPoss', 'OppPoss', 'OppMins', 'GameOT', 'OppWin', 'isRegularSeason', ]:
    del df[x]
    print(f"Deleted {x}")

for metr in METRICS:
    for pref in PREFIXES:
        try:
            del df[f'{pref}{metr}']
            print(f'Deleted {pref}{metr}')
        except KeyError:
            pass
            print(f"Skipping {pref}{metr}")
        try:
            del df[f'OppSum_{pref}{metr}']
            print(f'Deleted OppSum_{pref}{metr}')
        except KeyError:
            pass
            print(f'Skipping OppSum_{pref}{metr}')

for col in df.columns:
    if col[:6] == 'OppSum':
        del df[col]
        print(f"Deleted {col}")

Deleted TmWin
Deleted TmMins
Deleted OppGame
Deleted TmPoss
Deleted OppPoss
Deleted OppMins
Deleted GameOT
Deleted OppWin
Deleted isRegularSeason
Deleted TmPF
Deleted OppSum_TmPF
Deleted OppPF
Deleted OppSum_OppPF
Deleted TmMargin
Deleted OppSum_TmMargin
Deleted OppMargin
Deleted OppSum_OppMargin
Deleted TmFGM
Deleted OppSum_TmFGM
Deleted OppFGM
Deleted OppSum_OppFGM
Deleted TmFGA
Deleted OppSum_TmFGA
Deleted OppFGA
Deleted OppSum_OppFGA
Deleted TmFG3M
Deleted OppSum_TmFG3M
Deleted OppFG3M
Deleted OppSum_OppFG3M
Deleted TmFG3A
Deleted OppSum_TmFG3A
Deleted OppFG3A
Deleted OppSum_OppFG3A
Deleted TmFG2M
Deleted OppSum_TmFG2M
Deleted OppFG2M
Deleted OppSum_OppFG2M
Deleted TmFG2A
Deleted OppSum_TmFG2A
Deleted OppFG2A
Deleted OppSum_OppFG2A
Deleted TmFTA
Deleted OppSum_TmFTA
Deleted OppFTA
Deleted OppSum_OppFTA
Deleted TmFTM
Deleted OppSum_TmFTM
Deleted OppFTM
Deleted OppSum_OppFTM
Deleted TmAst
Deleted OppSum_TmAst
Deleted OppAst
Deleted OppSum_OppAst
Deleted TmORB
Deleted OppSum_TmORB
Del

In [39]:
df.columns

Index(['TmName', 'Season', 'TmGame', 'dataPriorTo', 'TmPFper40',
       'OA_TmPFper40', 'TmMarginper40', 'OA_TmMarginper40', 'TmFGMper40',
       'OA_TmFGMper40', 'TmFGAper40', 'OA_TmFGAper40', 'TmFG3Mper40',
       'OA_TmFG3Mper40', 'TmFG3Aper40', 'OA_TmFG3Aper40', 'TmFG2Mper40',
       'OA_TmFG2Mper40', 'TmFG2Aper40', 'OA_TmFG2Aper40', 'TmFTAper40',
       'OA_TmFTAper40', 'TmFTMper40', 'OA_TmFTMper40', 'TmAstper40',
       'OA_TmAstper40', 'TmORBper40', 'OA_TmORBper40', 'TmDRBper40',
       'OA_TmDRBper40', 'TmTRBper40', 'OA_TmTRBper40', 'TmTOper40',
       'OA_TmTOper40', 'TmStlper40', 'OA_TmStlper40', 'TmBlkper40',
       'OA_TmBlkper40', 'TmFoulper40', 'OA_TmFoulper40', 'OppPFper40',
       'OA_OppPFper40', 'OppMarginper40', 'OA_OppMarginper40', 'OppFGMper40',
       'OA_OppFGMper40', 'OppFGAper40', 'OA_OppFGAper40', 'OppFG3Mper40',
       'OA_OppFG3Mper40', 'OppFG3Aper40', 'OA_OppFG3Aper40', 'OppFG2Mper40',
       'OA_OppFG2Mper40', 'OppFG2Aper40', 'OA_OppFG2Aper40', 'OppFTAper4

In [40]:
df.head()

TmName  Season  TmGame dataPriorTo  TmPFper40  OA_TmPFper40  \
0   Alabama    2003       1  2002-11-15       68.0           NaN   
1   Memphis    2003       1  2002-11-15       70.0           NaN   
2  Oklahoma    2003       1  2002-11-15       62.0           NaN   
3  Syracuse    2003       1  2002-11-15       63.0           NaN   
4   Alabama    2003       1  2002-11-16       68.0           NaN   

   TmMarginper40  OA_TmMarginper40  TmFGMper40  OA_TmFGMper40  ...  \
0            6.0               NaN        27.0            NaN  ...   
1            7.0               NaN        26.0            NaN  ...   
2           -6.0               NaN        22.0            NaN  ...   
3           -7.0               NaN        24.0            NaN  ...   
4            6.0               NaN        27.0            NaN  ...   

   OppTOper40  OA_OppTOper40  OppStlper40  OA_OppStlper40  OppBlkper40  \
0        18.0            NaN          9.0             NaN          2.0   
1        12.0            NaN          8.0             NaN          6.0   
2        23.0            NaN          7.0             NaN          1.0   
3        13.0            NaN          4.0             NaN          4.0   
4        18.0            NaN          9.0             NaN          2.0   

   OA_OppBlkper40  OppFoulper40  OA_OppFoulper40  TmWinPct  TmPossPerGame  
0             NaN          20.0              NaN       1.0      72.672337  
1             NaN          16.0              NaN       1.0      67.992083  
2             NaN          22.0              NaN       0.0      72.672337  
3             NaN          18.0              NaN       0.0      67.992083  
4             NaN          20.0              NaN       1.0      72.672337  

[5 rows x 78 columns]

In [41]:
df.tail()

TmName  Season  TmGame dataPriorTo  TmPFper40  OA_TmPFper40  \
43568      Wright St    2020      30  2020-03-11  78.880658      6.623998   
43569        Wyoming    2020      32  2020-03-11  61.405405     -8.940613   
43570         Xavier    2020      31  2020-03-11  69.375494      0.665720   
43571           Yale    2020      28  2020-03-11  71.965517      2.905688   
43572  Youngstown St    2020      31  2020-03-11  70.342629     -1.661695   

       TmMarginper40  OA_TmMarginper40  TmFGMper40  OA_TmFGMper40  ...  \
43568       8.559671          5.499830   27.884774       2.255537  ...   
43569      -7.783784         -6.093186   21.096525      -3.886867  ...   
43570       3.256917          6.852959   25.486166       1.255178  ...   
43571       7.862069          7.332788   25.482759       0.611597  ...   
43572      -0.764940         -2.803053   25.274900      -0.183675  ...   

       OppTOper40  OA_OppTOper40  OppStlper40  OA_OppStlper40  OppBlkper40  \
43568   13.827160       0.504242     6.156379        0.047856     3.028807   
43569   12.725869       0.004540     5.868726        0.019635     2.501931   
43570   12.837945       0.014304     6.924901        0.520130     3.288538   
43571   11.275862      -1.572508     6.551724        0.556156     3.034483   
43572   11.250996      -2.303268     5.768924       -0.357309     3.346614   

       OA_OppBlkper40  OppFoulper40  OA_OppFoulper40  TmWinPct  TmPossPerGame  
43568        0.057123     20.345679         2.237714  0.766667      72.675260  
43569       -0.393846     17.359073         0.252234  0.250000      66.929314  
43570       -0.315095     17.770751         0.190705  0.612903      69.284619  
43571       -0.228575     16.275862        -0.545917  0.750000      69.009580  
43572        0.491093     16.956175        -1.389006  0.516129      67.365708  

[5 rows x 78 columns]

In [71]:
db = get_db()
games = pd.DataFrame(
    list(
        db.games.find(
            {'Season': {'$gte': 2003}},
            {'_id': 0, 'TmName': 1, 'OppName': 1, 'Season': 1, 'GameDate': 1, 'TmMargin': 1, 'GameVegasLine': 1, 'TmLoc': 1}
        )
    )
)


Connected to database: dev


In [72]:
games.shape

(185664, 8)

In [73]:
# De-dupe games - Keep home team or earler name in neutral games
games = games.loc[((games['TmLoc'] == 'H') | ((games['TmLoc'] == 'N') & (games['TmName'] < games['OppName'])))]
games = games.loc[np.abs(games['GameVegasLine']) <= 50]
games.shape

(60856, 8)

In [74]:
games.tail()

_id   GameDate         OppName  Season TmLoc  \
185611  5efe491c99070a609ada581a 2019-02-23  Col Charleston    2019     H   
185612  5efe491c99070a609ada581b 2020-01-09  Col Charleston    2020     H   
185615  5efe491c99070a609ada5878 2014-01-10         Radford    2014     H   
185651  5efe491c99070a609ada5a40 2019-01-21            NJIT    2019     H   
185653  5efe491c99070a609ada5a71 2020-01-22           Lamar    2020     H   

                TmName  TmMargin  GameVegasLine  
185611            Elon       -10           -8.5  
185612            Elon        -8           -9.0  
185615      High Point        -9            2.0  
185651   North Florida        -4            5.5  
185653  Incarnate Word       -12           -7.0

In [64]:
# GameVegasLine is the expected Tm margin. Positive means vegas favored Tm.
fig = px.scatter(games, x='TmMargin', y='GameVegasLine')
fig.show()

In [76]:
# If TmMargin > GameVegasLine: Team outperformed vegas - bet on team. If TmMargin < GameVegasLine, team did worse than vegas expected - bet on Opp
games['TmVegasMargin'] = games['TmMargin'] - games['GameVegasLine']
fig = px.histogram(games, x='TmVegasMargin')
fig.show()

In [77]:
games.describe()

Season      TmMargin  GameVegasLine  TmVegasMargin
count  60856.000000  60856.000000   60856.000000   60856.000000
mean    2012.873735      4.495284       4.514469      -0.019185
std        4.935785     13.807287       8.524735      10.751540
min     2004.000000    -59.000000     -34.500000     -55.000000
25%     2009.000000     -5.000000      -1.500000      -7.000000
50%     2013.000000      5.000000       4.500000       0.000000
75%     2017.000000     13.000000      10.000000       7.000000
max     2020.000000     94.000000      46.000000      64.500000

In [86]:
games.rename(inplace=True, columns={
    'GameDate': 'dataPriorTo'
})
games.columns
games['dataPriorTo'] = pd.to_datetime(games['dataPriorTo'])
df['dataPriorTo'] = pd.to_datetime(df['dataPriorTo'])


In [87]:
dfTm1 = 
df = pd.merge(
    left=games,
    right=df,
    on=['TmName', 'Season', 'dataPriorTo'],
    how='left'
)

In [ ]:
rf = RandomForestRegressor(
    max_depth=5, 
    random_state=114492
)

In [88]:
df.columns


Index(['_id', 'dataPriorTo', 'OppName', 'Season', 'TmLoc', 'TmName',
       'TmMargin', 'GameVegasLine', 'TmVegasMargin', 'TmGame', 'TmPFper40',
       'OA_TmPFper40', 'TmMarginper40', 'OA_TmMarginper40', 'TmFGMper40',
       'OA_TmFGMper40', 'TmFGAper40', 'OA_TmFGAper40', 'TmFG3Mper40',
       'OA_TmFG3Mper40', 'TmFG3Aper40', 'OA_TmFG3Aper40', 'TmFG2Mper40',
       'OA_TmFG2Mper40', 'TmFG2Aper40', 'OA_TmFG2Aper40', 'TmFTAper40',
       'OA_TmFTAper40', 'TmFTMper40', 'OA_TmFTMper40', 'TmAstper40',
       'OA_TmAstper40', 'TmORBper40', 'OA_TmORBper40', 'TmDRBper40',
       'OA_TmDRBper40', 'TmTRBper40', 'OA_TmTRBper40', 'TmTOper40',
       'OA_TmTOper40', 'TmStlper40', 'OA_TmStlper40', 'TmBlkper40',
       'OA_TmBlkper40', 'TmFoulper40', 'OA_TmFoulper40', 'OppPFper40',
       'OA_OppPFper40', 'OppMarginper40', 'OA_OppMarginper40', 'OppFGMper40',
       'OA_OppFGMper40', 'OppFGAper40', 'OA_OppFGAper40', 'OppFG3Mper40',
       'OA_OppFG3Mper40', 'OppFG3Aper40', 'OA_OppFG3Aper40', 'OppFG2M